### Packages

In [ ]:
!pip install spektral
!pip install lime
!pip install rdkit
!pip install py3Dmol
!pip install Bio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.1/140.1 kB 1.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.0/5.0 MB 21.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 275.7/275.7 kB 2.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for lime: filename=lime-0.2.0.1-py3-none-any.whl size=283835 sha256=e2242514a3ab3fb18eae1acde5ef7a81289955f6435df074c1be03024970eaa0
  Stored in directory: /root/.cache/pip/wheels/fd/a2/af/9ac0a1a85a27f314a06b39e1f492bee1547d52549a4606ed89
Successfully built lime
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 33.1/33.1 MB 32.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 281.0/281.0 kB 2.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 21.1 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

from keras.layers import concatenate
from tensorflow.keras import backend as K

from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.layers import Input, Embedding, LSTM, Dropout, BatchNormalization, Dense, concatenate, Reshape, Flatten, Attention, Bidirectional, MultiHeadAttention
from tensorflow.keras.optimizers import Adam, AdamW
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau, ModelCheckpoint

from tensorflow.keras.metrics import RootMeanSquaredError
from tensorflow.keras.regularizers import l2
from tensorflow.keras.initializers import GlorotUniform

from spektral.layers import GCNConv, GlobalSumPool, GATConv
from scipy.sparse import csr_matrix

from rdkit import Chem
from rdkit.Chem import AllChem
from rdkit.Chem import Draw
from rdkit.Chem.Draw import rdMolDraw2D

import lime
from lime.lime_tabular import LimeTabularExplainer

from IPython.display import display, Image

from collections import defaultdict

import py3Dmol

from Bio import SeqIO
from Bio.pairwise2 import align

/usr/local/lib/python3.10/dist-packages/Bio/pairwise2.py:278: BiopythonDeprecationWarning: Bio.pairwise2 has been deprecated, and we intend to remove it in a future release of Biopython. As an alternative, please consider using Bio.Align.PairwiseAligner as a replacement, and contact the Biopython developers if you still need the Bio.pairwise2 module.
  warnings.warn(


### LIME Explainations

In [ ]:
train_df = pd.read_pickle('/content/drive/MyDrive/Dataframes/train_df.pkl')
test_df = pd.read_pickle('/content/drive/MyDrive/Dataframes/test_df.pkl')

In [ ]:
test_dfs_by_pdb_id = {pdb_id: test_df_group for pdb_id, test_df_group in test_df.groupby('pdb_id')}

for pdb_id in test_dfs_by_pdb_id.keys():
    globals()[f"test_df_{pdb_id}"] = test_dfs_by_pdb_id[pdb_id]

print([f"test_df_{pdb_id}" for pdb_id in test_dfs_by_pdb_id.keys()])

['test_df_1T7R', 'test_df_2ZV2', 'test_df_4F8H', 'test_df_5EK0', 'test_df_6D6T', 'test_df_6IIU']


In [ ]:
fingerprints_model = load_model('/content/drive/MyDrive/Saved_Models/fingerprints_best_model.h5', custom_objects={'r2_score': r2_score, 'GCNConv': GCNConv, 'GATConv': GATConv})

In [ ]:
aa_alphabet = {'A': 1, 'C': 2, 'D': 3, 'E': 4, 'F': 5, 'G': 6, 'H': 7, 'I': 8, 'K': 9, 'L': 10, 'M': 11, 'N': 12, 'P': 13, 'Q': 14, 'R': 15, 'S': 16, 'T': 17, 'V': 18, 'W': 19, 'Y': 20}

In [ ]:
sequences = {
    "6IIU": "DYKDDDDGAPADLEDNWETLNDNLKVIEKADNAAQVKDALTKMRAAALDAQKATPPKLEDKSPDSPEMKDFRHGFDILVGQIDDALKLANEGKVKEAQAAAEQLKTTRNAYIQKYLPCFRPTNITLEERRLIASPWFAASFCVVGLASNLLALSVLAGARQGGSHTRSSFLTFLCGLVLTDFLGLLVTGTIVVSQHAALFEWHAVDPGCRLCRFMGVVMIFFGLSPLLLGAAMASERYLGITRPFSRPAVASQRRAWATVGLVWAAALALGLLPLLGVGRYTVQYPGSWCFLTLGAESGDVAFGLLFSMLGGLSVGLSFLLNTVSVATLCHVYHGMKKYTCTVCGYIYNPEDGDPDNGVNPGTDFKDIPDDWVCPLCGVGKDQFEEVEERDSEVEMMAQALGIMVVASVCWLPLLVFIAQTVLRNPPAMSPAGQLSRTTEKELLIYLRVATWNQILDPWVYILFRRAVLRRLQPRLEFLEVLFQ",
    "2ZV2": "GSSGSSGDCVQLNQYTLKDEIGKGSYGVVKLAYNENDNTYYAMKVLSKKKLIRQAGFPRRPPPRGTRPAPGGCIQPRGPIEQVYQEIAILKKLDHPNVVKLVEVLDDPNEDHLYMVFELVNQGPVMEVPTLKPLSEDQARFYFQDLIKGIEYLHYQKIIHRDIKPSNLLVGEDGHIKIADFGVSNEFKGSDALLSNTVGTPAFMAPESLSETRKIFSGKALDVWAMGVTLYCFVFGQCPFMDERIMCLHSKIKSQALEFPDQPDIAEDLKDLITRMLDKNPESRIVVPEIKLHPWVTR",
    "6D6T": "QSVNDPSNMSLVKETVDRLLKGYDIRLRPDFGGPPVAVGMNIDIASIDMVSEVNMDYTLTMYFQQAWRDKRLSYNVIPLNLTLDNRVADQLWVPDTYFLNDKKSFVHGVTVKNRMIRLHPDGTVLYGLRITTTAACMMDLRRYPLDEQNCTLEIESYGYTTDDIEFYWRGDDNAVTGVTKIELPQFSIVDYKLITKKVVFSTGSYPRLSLSFKLKRNIGYFILQTYMPSILITILSWVSFWINYDASAARVALGITTVLTMTTINTHLRETLPKIPYVKAIDMYLMGCFVFVFMALLEYALVNYIFFSQPARAAAIDRWSRIFFPVVFSFFNIVYWLYYVN",
    "5EK0": "MDYKDDDDKGSLVPRGSHMYLRITNIVESSFFTKFIIYLIVLNMVTMMVEKEGQSQHMTEVLYWINVVFIILFTIEIILRIYVHRISFFKDPWSLFDFVVVIISIVGMFLADLIETYFVSPTLFRVIRLARIGRILRLVTAVPQMRKIVSALISVIPGMLSVIALMTLFFYIFAIMATQLFGERFPEWFGTLGESFYTLFQVMTLESWSMGIVRPLMEVYPYAWVFFIPFIFVVTFVMINLVVAIIVDAMAILNQKEEQHIIDEVQSHEDNINNEIIKLREEIVELKELIKTSLKN",
    "4F8H": "GQDMVSPPPPIADEPLTVNTGIYLIECYSLDDKAETFKVNAFLSLSWKDRRLAFDPVRSGVRVKTYEPEAIWIPEIRFVNVENARDADVVDISVSPDGTVQYLERFSARVLSPLDFRRYPFDSQTLHIYLIVRSVDTRNIVLAVDLEKVGKNDDVFLTGWDIESFTAVVKPANFALEDRLESKLDYQLRISRQYFSYIPNIILPMLFILFISWTAFWSTSYEANVTLVVSTLIAHIAFNILVETNLPKTPYMTYTGAIIFMIYLFYFVAVIEVTVQHYLKVESQPARAASITRASRIAFPVVFLLANIILAFLFFGF",
    "1T7R": "GSPGISGGGGGSHIEGYECQPIFLNVLEAIEPGVVCAGHDNNQPDSFAALLSSLNELGERQLVHVVKWAKALPGFRNLHVDDQMAVIQYSWMGLMVFAMGWRSFTNVNSRMLYFAPDLVFNEYRMHKSRMYSQCVRMRHLSQEFGWLQITPQEFLCMKALLLFSIIPVDGLKNQKFFDELRMNYIKELDRIIACKRKNPTSCSRRFYQLTKLLDSVQPIARELHQFTFDLLIKSHMVSVDFPEMMAEIISVQVPKILSGKVKPIYFHTQ"
}
#https://www.rcsb.org/fasta/entry/pdb_id/display

In [ ]:
X_text_train = np.array([np.array(x) for x in train_df['encoded_seq'].tolist()])
X_extended_connectivity_train = np.array(train_df['extended_connectivity_fps'].tolist())

combined_train_data = np.concatenate((X_extended_connectivity_train, X_text_train), axis=1)

explainer = LimeTabularExplainer(
    training_data=combined_train_data,
    feature_names= [f'rec_{i}' for i in range(X_text_train.shape[1])] + [f'bit_{i}' for i in range(1024)] ,
    class_names=['output'],
    mode='regression'
)

In [ ]:
def predict_fn(features):
    connectivity_features = features[:, :X_extended_connectivity_input.shape[1]]
    text_features = features[:, X_extended_connectivity_input.shape[1]:]
    return fingerprints_model.predict([text_features, connectivity_features])

def decode_sequence(encoded_sequence):
    decoded_sequence = ''
    for aa in encoded_sequence:
        if aa != 0:
            decoded_sequence += list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa)]
    return decoded_sequence

#### 4F8H

In [ ]:
pdb_id = '4F8H'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

1656/1656 [==============================] - 733s 442ms/step
Predictions for 4F8H are complete.


In [ ]:
threshold = 0.001
well_predicted_dfs_by_pdb_id = {}

pdb_id = '4F8H'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 4F8H: 31


In [ ]:
df_4F8H = well_predicted_dfs_by_pdb_id['4F8H']
df_4F8H.head(2)

pdb_id           zinc_id  docking_score  \
5755   4F8H  ZINC001150567179      -6.607286   
6949   4F8H  ZINC001760502527      -6.442638   

                                                 smiles  \
5755  Cc1[nH][nH]c2ncnc(=NC(=O)c3cc4cnccc4nc3C(F)(F)...   
6949  C=CCN(CCOC)c1nnc(-c2ccc[nH]2)n1C[C@@]1(O)CCCC1...   

                                               sequence  \
5755  GQDMVSPPPPIADEPLTVNTGIYLIECYSLDDKAETFKVNAFLSLS...   
6949  GQDMVSPPPPIADEPLTVNTGIYLIECYSLDDKAETFKVNAFLSLS...   

                                            encoded_seq  molecular_weight  \
5755  [6, 14, 3, 11, 18, 16, 13, 13, 13, 13, 8, 1, 3...          0.052049   
6949  [6, 14, 3, 11, 18, 16, 13, 13, 13, 13, 8, 1, 3...          0.056357   

          logP  numH_donors  numH_acceptors  \
5755 -0.280790     0.687259        0.134442   
6949  0.174244     0.687259        0.751344   

                              extended_connectivity_fps  \
5755  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
6949  [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 1, 0, ...   

                                          node_features  \
5755  [6.0, 6.0, 7.0, 7.0, 6.0, 7.0, 6.0, 7.0, 6.0, ...   
6949  [6.0, 6.0, 6.0, 7.0, 6.0, 6.0, 8.0, 6.0, 6.0, ...   

                                          edge_features  \
5755  [1.0, 1.5, 1.5, 1.5, 1.5, 1.5, 1.5, 1.5, 2.0, ...   
6949  [2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.5, ...   

                                       adjacency_matrix  predicted_scores  \
5755  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...          -6.60652   
6949  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...          -6.44195   

      difference  
5755    0.000766  
6949    0.000688

In [ ]:
X_text_input = np.array([np.array(x) for x in df_4F8H['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_4F8H['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_4F8H)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

157/157 [==============================] - 69s 441ms/step


In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           S     0.077883  [rec_106, rec_28, rec_28, rec_229, rec_229, re...   
1           A    -0.229285                 [rec_297, rec_287, rec_52, rec_52]   
2           E     0.894942      [rec_146, rec_103, rec_176, rec_103, rec_103]   
3           D     0.392651  [rec_48, rec_54, rec_48, rec_153, rec_48, rec_...   
4           Y    -0.009554                         [rec_185, rec_196, rec_22]   
5           F     0.275344  [rec_298, rec_173, rec_173, rec_313, rec_164, ...   
6           I    -0.202129  [rec_91, rec_290, rec_307, rec_290, rec_91, re...   
7           N     0.206640  [rec_244, rec_172, rec_151, rec_238, rec_82, r...   
8           R     0.006956  [rec_49, rec_49, rec_286, rec_57, rec_137, rec...   
9           V     0.197211  [rec_167, rec_228, rec_60, rec_88, rec_224, re...   
10          P    -0.097878         [rec_95, rec_55, rec_170, rec_95, rec_299]   
11          L    -0.112655                [rec_129, rec_44, rec_183, rec_278]   
12          W     1.052988                                           [rec_71]   
13          K    -0.272089                        [rec_150, rec_279, rec_247]   
14          Q    -0.342985                                 [rec_100, rec_100]   
15          T    -0.934537                                  [rec_35, rec_230]   
16          H    -1.809064                                          [rec_234]   
17          M    -1.138490                                          [rec_260]   
18          G    -0.624356                                           [rec_20]   

                                              Weights  
0   [1.2279775997292994, -0.48143911090250857, -0....  
1   [-1.0796227727851504, -0.8891813853801334, 1.9...  
2   [0.8350814299923663, 0.9796630978885261, 0.985...  
3   [-0.7926981769291895, 0.24884236026816964, 1.0...  
4   [0.9758163178642961, 0.05578679841180786, -1.0...  
5   [0.9706027602053364, -0.8521338114339255, 0.52...  
6   [-0.8617642912103771, -1.4066477741776888, -0....  
7   [-0.6686376612431421, 0.780876446318766, -0.92...  
8   [0.8934331154183511, 0.7152871695319899, -1.17...  
9   [0.8836612147969571, 1.3538213914366761, 0.790...  
10  [1.1527127700757933, -0.9656193037935332, 1.08...  
11  [0.6024741812727057, -1.2064523999840737, 1.24...  
12                               [1.0529881744595808]  
13  [-0.7095302432917547, -1.3863936608111211, 1.2...  
14          [-0.0955181588622078, -0.590451056705397]  
15          [-1.0857726928765437, -0.783300906537418]  
16                               [-1.809063742508988]  
17                              [-1.1384897567941596]  
18                              [-0.6243563585138259]

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           S     0.077883                        [rec_106, rec_229, rec_229]   
2           E     0.894942               [rec_146, rec_103, rec_176, rec_103]   
3           D     0.392651  [rec_54, rec_48, rec_153, rec_48, rec_152, rec...   
5           F     0.275344               [rec_298, rec_173, rec_313, rec_120]   
7           N     0.206640       [rec_172, rec_238, rec_82, rec_199, rec_172]   
8           R     0.006956  [rec_49, rec_49, rec_178, rec_292, rec_292, re...   
9           V     0.197211         [rec_167, rec_228, rec_60, rec_88, rec_89]   
12          W     1.052988                                           [rec_71]   

                                              Weights  
0   [1.2279775997292994, 0.8630988930132094, 0.300...  
2   [0.8350814299923663, 0.9796630978885261, 0.985...  
3   [0.24884236026816964, 1.0084652976211246, 1.06...  
5   [0.9706027602053364, 0.5274863660525659, 1.169...  
7   [0.780876446318766, 0.3842529457284937, 0.9442...  
8   [0.8934331154183511, 0.7152871695319899, 1.389...  
9   [0.8836612147969571, 1.3538213914366761, 0.790...  
12                               [1.0529881744595808]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

['rec_106', 'rec_229', 'rec_229', 'rec_146', 'rec_103', 'rec_176', 'rec_103', 'rec_54', 'rec_48', 'rec_153', 'rec_48', 'rec_152', 'rec_48', 'rec_152', 'rec_48', 'rec_298', 'rec_173', 'rec_313', 'rec_120', 'rec_172', 'rec_238', 'rec_82', 'rec_199', 'rec_172', 'rec_49', 'rec_49', 'rec_178', 'rec_292', 'rec_292', 'rec_292', 'rec_167', 'rec_228', 'rec_60', 'rec_88', 'rec_89', 'rec_71']


In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [106, 229, 229, 146, 103, 176, 103, 54, 48, 153, 48, 152, 48, 152, 48, 298, 173, 313, 120, 172, 238, 82, 199, 172, 49, 49, 178, 292, 292, 292, 167, 228, 60, 88, 89, 71]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/4f8h.pdb'
input_sequence = 'GQDMVSPPPPIADEPLTVNTGIYLIECYSLDDKAETFKVNAFLSLSWKDRRLAFDPVRSGVRVKTYEPEAIWIPEIRFVNVENARDADVVDISVSPDGTVQYLERFSARVLSPLDFRRYPFDSQTLHIYLIVRSVDTRNIVLAVDLEKVGKNDDVFLTGWDIESFTAVVKPANFALEDRLESKLDYQLRISRQYFSYIPNIILPMLFILFISWTAFWSTSYEANVTLVVSTLIAHIAFNILVETNLPKTPYMTYTGAIIFMIYLFYFVAVIEVTVQHYLKVESQPARAASITRASRIAFPVVFLLANIILAFLFFGF'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
print(mapped_residues)

{48: 11, 49: 11, 54: 12, 60: 13, 71: 14, 82: 16, 88: 17, 89: 17, 103: 19, 106: 19, 120: 22, 146: 24, 152: 25, 153: 25, 167: 27, 172: 28, 173: 28, 176: 28, 178: 28, 199: 31, 228: 35, 229: 35, 238: 36, 292: 42, 298: 43, 313: 45}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [11, 11, 12, 13, 14, 16, 17, 17, 19, 19, 22, 24, 25, 25, 27, 28, 28, 28, 28, 31, 35, 35, 36, 42, 43, 45]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/4f8h.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

Output hidden; open in https://colab.research.google.com to view.

#### 2ZV2

In [ ]:
pdb_id = '2ZV2'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

438/438 [==============================] - 194s 442ms/step
Predictions for 2ZV2 are complete.


In [ ]:
threshold = 0.25
well_predicted_dfs_by_pdb_id = {}

pdb_id = '2ZV2'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 2ZV2: 17


In [ ]:
df_2ZV2 = well_predicted_dfs_by_pdb_id['2ZV2']
df_2ZV2.head(2)

pdb_id           zinc_id  docking_score  \
5371    2ZV2  ZINC001077117205     -11.002764   
43241   2ZV2  ZINC000629151062     -11.010069   

                                                 smiles  \
5371   O=C(N[C@@H]1CN(C/C=C\Cl)C[C@H]1O)c1cc2c(o1)CCCC2   
43241          O=C(c1ccnc(N2CCOCC2)n1)N1CCc2c(O)cccc2C1   

                                                sequence  \
5371   GSSGSSGDCVQLNQYTLKDEIGKGSYGVVKLAYNENDNTYYAMKVL...   
43241  GSSGSSGDCVQLNQYTLKDEIGKGSYGVVKLAYNENDNTYYAMKVL...   

                                             encoded_seq  molecular_weight  \
5371   [6, 16, 16, 6, 16, 16, 6, 3, 2, 18, 14, 10, 12...         -0.976797   
43241  [6, 16, 16, 6, 16, 16, 6, 3, 2, 18, 14, 10, 12...         -0.646332   

           logP  numH_donors  numH_acceptors  \
5371  -0.705120     0.687259       -0.482460   
43241 -1.058026    -0.370547        0.751344   

                               extended_connectivity_fps  \
5371   [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
43241  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           node_features  \
5371   [8.0, 6.0, 7.0, 6.0, 6.0, 7.0, 6.0, 6.0, 6.0, ...   
43241  [8.0, 6.0, 6.0, 6.0, 6.0, 7.0, 6.0, 7.0, 6.0, ...   

                                           edge_features  \
5371   [2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, ...   
43241  [2.0, 1.0, 1.5, 1.5, 1.5, 1.5, 1.0, 1.0, 1.0, ...   

                                        adjacency_matrix  predicted_scores  \
5371   [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...        -10.764606   
43241  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...        -10.776500   

       difference  
5371     0.238158  
43241    0.233569

In [ ]:
X_text_input = np.array([np.array(x) for x in df_2ZV2['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_2ZV2['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_2ZV2)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

157/157 [==============================] - 70s 442ms/step


In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           F     0.429634                [rec_234, rec_234, rec_56, rec_234]   
1           T    -0.175964  [rec_273, rec_296, rec_228, rec_199, rec_199, ...   
2           Q     0.679327                                 [rec_137, rec_254]   
3           K     0.102456  [rec_290, rec_156, rec_269, rec_187, rec_48, r...   
4           S     0.874213                                 [rec_183, rec_189]   
5           P    -0.453403         [rec_60, rec_132, rec_62, rec_57, rec_164]   
6           Y     0.457627                        [rec_141, rec_154, rec_141]   
7           A     0.118695                                 [rec_201, rec_224]   
8           V     0.238889   [rec_28, rec_82, rec_28, rec_44, rec_82, rec_44]   
9           I     0.870723                  [rec_20, rec_264, rec_88, rec_88]   
10          G    -0.217092                           [rec_0, rec_170, rec_55]   
11          N     0.389730                                           [rec_35]   
12          D     0.089619                                  [rec_18, rec_161]   
13          E     0.397975                                          [rec_109]   
14          L     0.515426                                   [rec_89, rec_89]   

                                              Weights  
0   [1.59426056790294, -1.0639827340285668, 0.3228...  
1   [-0.9909963898361328, 1.1887986609129686, -0.6...  
2           [0.8714903127408707, 0.48716382842571326]  
3   [-1.4663123155891031, -1.1830556282663565, -0....  
4            [2.886145684590237, -1.1377203396796292]  
5   [-0.9486310252599953, 1.263688698735484, 0.772...  
6   [-0.9058223394671119, 0.8936978688485372, 1.38...  
7          [0.6963101870431984, -0.45892030299085274]  
8   [-0.018562254823656314, 1.2932509011077937, 1....  
9   [-0.44326848176097533, 0.8513632594697363, 1.3...  
10  [-1.3200052492635024, -1.0126255865255362, 1.6...  
11                              [0.38973015698714697]  
12           [-1.0155710792315675, 1.194810028102442]  
13                               [0.3979747816028723]  
14          [0.24677468087694737, 0.7840775470059391]

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                            rec_ids  \
0           F     0.429634         [rec_234, rec_56, rec_234]   
2           Q     0.679327                 [rec_137, rec_254]   
3           K     0.102456  [rec_48, rec_22, rec_163, rec_48]   
4           S     0.874213                          [rec_183]   
6           Y     0.457627                 [rec_154, rec_141]   
7           A     0.118695                          [rec_201]   
8           V     0.238889           [rec_82, rec_28, rec_44]   
9           I     0.870723          [rec_264, rec_88, rec_88]   
11          N     0.389730                           [rec_35]   
12          D     0.089619                          [rec_161]   
13          E     0.397975                          [rec_109]   
14          L     0.515426                   [rec_89, rec_89]   

                                              Weights  
0   [1.59426056790294, 0.3228284439534767, 0.86542...  
2           [0.8714903127408707, 0.48716382842571326]  
3   [1.2004365622400106, 1.7578386078481378, 0.747...  
4                                 [2.886145684590237]  
6             [0.8936978688485372, 1.385006595198181]  
7                                [0.6963101870431984]  
8   [1.2932509011077937, 1.8440364014913353, 0.083...  
9   [0.8513632594697363, 1.3919403176301206, 1.682...  
11                              [0.38973015698714697]  
12                                [1.194810028102442]  
13                               [0.3979747816028723]  
14          [0.24677468087694737, 0.7840775470059391]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

['rec_234', 'rec_56', 'rec_234', 'rec_137', 'rec_254', 'rec_48', 'rec_22', 'rec_163', 'rec_48', 'rec_183', 'rec_154', 'rec_141', 'rec_201', 'rec_82', 'rec_28', 'rec_44', 'rec_264', 'rec_88', 'rec_88', 'rec_35', 'rec_161', 'rec_109', 'rec_89', 'rec_89']


In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [234, 56, 234, 137, 254, 48, 22, 163, 48, 183, 154, 141, 201, 82, 28, 44, 264, 88, 88, 35, 161, 109, 89, 89]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/2zv2.pdb'
input_sequence = 'GSSGSSGDCVQLNQYTLKDEIGKGSYGVVKLAYNENDNTYYAMKVLSKKKLIRQAGFPRRPPPRGTRPAPGGCIQPRGPIEQVYQEIAILKKLDHPNVVKLVEVLDDPNEDHLYMVFELVNQGPVMEVPTLKPLSEDQARFYFQDLIKGIEYLHYQKIIHRDIKPSNLLVGEDGHIKIADFGVSNEFKGSDALLSNTVGTPAFMAPESLSETRKIFSGKALDVWAMGVTLYCFVFGQCPFMDERIMCLHSKIKSQALEFPDQPDIAEDLKDLITRMLDKNPESRIVVPEIKLHPWVTR'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

Alignments: [Alignment(seqA='VALVALVALVALVALVALVALGLNGLNGLNGLNGLNGLNGLNGLNGLNLEULEULEULEULEULEULEULEUASNASNASNASNASNASNA-SNASNGLNGLNGLNGLNGLNGLNGLNGLNG----LNTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRT-YRTHRTHRTHRTHRTHRTHRTHRLEULEULEULEULEULEULEULEULYSLYSLYSLYSLYSLYSLYSLYSLYSASPASPASPASPASPASPASPASPGLUGLUGLUGLUGLUGLUGLUGLUGLUILEILEILEILEILEILEIL--EILEGLYGLYGLY-GLYLYSLYSLYSLYSLYSLYSLYSLYSLYSTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRGLYGLYGLYGLYVALVALVALVALVALVALVALVALVALVALVALVALVALVALLYSLYSLYSLYSLYSLYSLYSLYSLYSLEULEULEULEULEULEULEULEUALAALAALAALAA-LATYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRASNASNASNASNASNASNASNASNGLUGLUGLUGLUGLUGLUGLUGLUGLUASNASNASNASNASNASNASNASNASPASPASPASPASPASPASPASPASNASNASNASNASNASNAS-NAS-NTHRTHRTHRTHRTHRTHRTHRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRTYRALAALAALAALAALAMETMETMETMETMETMETMETMETLYSLYSLYSLYSLYSLYSLYSLYSLYSVALVALVALVALVALVALVALLEULEULEULEULEULEULEULEUSERSERSERSERSERSERLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSLYSGLUGLUGLUGLUGLUGLUGLUGL

In [ ]:
print(mapped_residues)

{22: 163, 28: 164, 35: 165, 44: 166, 48: 166, 56: 167, 82: 170, 88: 171, 89: 171, 109: 174, 137: 179, 141: 180, 154: 181, 161: 182, 163: 183, 183: 185, 201: 187, 234: 191, 254: 193, 264: 194}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [163, 164, 165, 166, 166, 167, 170, 171, 171, 174, 179, 180, 181, 182, 183, 185, 187, 191, 193, 194]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/2zv2.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

#### 1T7R

In [ ]:
pdb_id = '1T7R'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

669/669 [==============================] - 300s 448ms/step
Predictions for 1T7R are complete.


In [ ]:
threshold = 0.001
well_predicted_dfs_by_pdb_id = {}

pdb_id = '1T7R'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 1T7R: 20


In [ ]:
df_1T7R = well_predicted_dfs_by_pdb_id['1T7R']
df_1T7R.head(2)

pdb_id           zinc_id  docking_score  \
5879   1T7R  ZINC000775844648      -3.432183   
7157   1T7R  ZINC000532071538      -3.402913   

                                                 smiles  \
5879  COc1ncc(/C=C/C(=O)N[C@H](c2ccccc2)c2ccc3c(c2)C...   
7157  COc1ccc(C(=O)Nc2ccc(C(=O)N3CCC[C@@H]3C3CCC3)s2...   

                                               sequence  \
5879  GSPGISGGGGGSHIEGYECQPIFLNVLEAIEPGVVCAGHDNNQPDS...   
7157  GSPGISGGGGGSHIEGYECQPIFLNVLEAIEPGVVCAGHDNNQPDS...   

                                            encoded_seq  molecular_weight  \
5879  [6, 16, 13, 6, 8, 16, 6, 6, 6, 6, 6, 16, 7, 8,...          0.649710   
7157  [6, 16, 13, 6, 8, 16, 6, 6, 6, 6, 6, 16, 7, 8,...          0.289751   

          logP  numH_donors  numH_acceptors  \
5879  0.834106    -0.370547        0.134442   
7157  1.349717    -0.370547       -0.482460   

                              extended_connectivity_fps  \
5879  [0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, ...   
7157  [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                          node_features  \
5879  [6.0, 8.0, 6.0, 7.0, 6.0, 6.0, 6.0, 6.0, 6.0, ...   
7157  [6.0, 8.0, 6.0, 6.0, 6.0, 6.0, 6.0, 8.0, 7.0, ...   

                                          edge_features  \
5879  [1.0, 1.0, 1.5, 1.5, 1.5, 1.0, 2.0, 1.0, 2.0, ...   
7157  [1.0, 1.0, 1.5, 1.5, 1.5, 1.0, 2.0, 1.0, 1.0, ...   

                                       adjacency_matrix  predicted_scores  \
5879  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...         -3.431965   
7157  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...         -3.401915   

      difference  
5879    0.000218  
7157    0.000998

In [ ]:
X_text_input = np.array([np.array(x) for x in df_1T7R['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_1T7R['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_1T7R)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

157/157 [==============================] - 70s 443ms/step


In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           A    -0.761618  [rec_48, rec_48, rec_28, rec_48, rec_48, rec_4...   
1           I     0.645813               [rec_247, rec_247, rec_164, rec_247]   
2           S    -1.031284                  [rec_89, rec_127, rec_89, rec_52]   
3           P    -0.060719                 [rec_20, rec_20, rec_217, rec_198]   
4           E    -0.133874  [rec_178, rec_55, rec_55, rec_55, rec_55, rec_...   
5           T     0.058461                        [rec_199, rec_199, rec_199]   
6           K    -0.348082                        [rec_254, rec_185, rec_254]   
7           R     1.503431                                          [rec_137]   
8           F     0.216757  [rec_240, rec_22, rec_240, rec_153, rec_103, r...   
9           V    -0.574485                                  [rec_238, rec_25]   
10          Y     0.637878                                  [rec_183, rec_88]   
11          M     0.276159                                  [rec_156, rec_91]   
12          L     0.413379  [rec_229, rec_56, rec_187, rec_229, rec_56, re...   
13          N    -0.757776                                           [rec_76]   
14          Q     0.318372                         [rec_60, rec_173, rec_141]   
15          H    -0.183509                                 [rec_234, rec_125]   
16          C     1.151933                                           [rec_35]   
17          G     0.130970                                    [rec_57, rec_0]   
18          D    -0.581627                         [rec_188, rec_228, rec_44]   

                                              Weights  
0   [-2.4067946685945865, -1.206027987487302, -1.7...  
1   [1.3577982419910704, 1.7088737127994196, 0.826...  
2   [-1.138160774539419, -1.3050884430742162, -0.8...  
3   [0.902292281538251, -1.072286420994698, 0.4584...  
4   [-0.8886218849745807, -0.04636252228378713, -0...  
5   [0.7407881456624384, 0.5172411100612517, -1.08...  
6   [-0.5969544489903694, -1.0395507407745888, 0.5...  
7                                [1.5034308725201437]  
8   [0.9280083201686611, -0.1617609852270674, 1.11...  
9          [-0.5976397371865191, -0.5513292962181653]  
10          [0.8881391702041095, 0.38761650660385455]  
11         [-0.20900030213432452, 0.7613177165676726]  
12  [0.7925496968518858, 0.6403883113521425, 1.417...  
13                              [-0.7577763819350073]  
14  [0.5925170438476274, 0.8722798651186033, -0.50...  
15          [-0.8865344430517762, 0.5195161068840876]  
16                               [1.1519325394303923]  
17          [0.9621576924243354, -0.7002182213609253]  
18  [-0.849094074896966, 0.5157934183395673, -1.41...

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                                            rec_ids  \
1           I     0.645813                        [rec_247, rec_247, rec_164]   
5           T     0.058461                                 [rec_199, rec_199]   
7           R     1.503431                                          [rec_137]   
8           F     0.216757               [rec_240, rec_240, rec_103, rec_176]   
10          Y     0.637878                                  [rec_183, rec_88]   
11          M     0.276159                                           [rec_91]   
12          L     0.413379  [rec_229, rec_56, rec_187, rec_154, rec_256, r...   
14          Q     0.318372                                  [rec_60, rec_173]   
16          C     1.151933                                           [rec_35]   
17          G     0.130970                                           [rec_57]   

                                              Weights  
1   [1.3577982419910704, 1.7088737127994196, 0.826...  
5            [0.7407881456624384, 0.5172411100612517]  
7                                [1.5034308725201437]  
8   [0.9280083201686611, 1.1160940457832413, 0.652...  
10          [0.8881391702041095, 0.38761650660385455]  
11                               [0.7613177165676726]  
12  [0.7925496968518858, 0.6403883113521425, 1.417...  
14           [0.5925170438476274, 0.8722798651186033]  
16                               [1.1519325394303923]  
17                               [0.9621576924243354]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

['rec_247', 'rec_247', 'rec_164', 'rec_199', 'rec_199', 'rec_137', 'rec_240', 'rec_240', 'rec_103', 'rec_176', 'rec_183', 'rec_88', 'rec_91', 'rec_229', 'rec_56', 'rec_187', 'rec_154', 'rec_256', 'rec_56', 'rec_170', 'rec_60', 'rec_173', 'rec_35', 'rec_57']


In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [247, 247, 164, 199, 199, 137, 240, 240, 103, 176, 183, 88, 91, 229, 56, 187, 154, 256, 56, 170, 60, 173, 35, 57]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/1t7r.pdb'
input_sequence = 'GSPGISGGGGGSHIEGYECQPIFLNVLEAIEPGVVCAGHDNNQPDSFAALLSSLNELGERQLVHVVKWAKALPGFRNLHVDDQMAVIQYSWMGLMVFAMGWRSFTNVNSRMLYFAPDLVFNEYRMHKSRMYSQCVRMRHLSQEFGWLQITPQEFLCMKALLLFSIIPVDGLKNQKFFDELRMNYIKELDRIIACKRKNPTSCSRRFYQLTKLLDSVQPIARELHQFTFDLLIKSHMVSVDFPEMMAEIISVQVPKILSGKVKPIYFHTQ'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

Alignments: [Alignment(seqA='CYSCYSCYSCYSCYSCYSGLNGLNGLN--GLN--GLNGLNGLNGLNGLNPROPROPROPROPROPROPROILEILEILEILEILEILEILEILEPHEPHEPHEPHEPHEPHEPHEPHEP-H-EPH--E--PHELEULEULEULEULEULEULEU--LEUASNASNASNASNASNASNASNASNVALVALVALVALVALVALVALLEULEULEULEULEULEULEULEUGLUGLUGLUGLUGLUGLUGLUGLUGLUALAALAALAALAALAILEILEILEILEILEILEILEILEGLUGLUGLUGLUGLUGLUGLUGLUGLUPROPROPROPROPROPROPROGLYGLYGLYGLYVALVALVALVALVALVALVALVALVALVALVALVALVALVALCYSCYSCYSCYSCYSCYSALAALAALAALAALAGLYGLYGLYGLYHISHISHISHISHISHISHISHISHISHISASPASPASPASPASPASPASPASPASNASNASNASNASNASNASNASNASNASNASNASNASNASNASNASNGLNGLNGLNGLNGLNGLNGLNGL-NGLNPROPROPROPROPROPROPROASPASPASPASPASPASPASPAS-PSERSERSERSERSER-SERPHEPHEPHEPHEPHEPHEPHEPHEPHEPHEPHEALAALAALAALAALAALAALAALAALA-ALALEULEULEULEULEULEULEULEULEULEULEULEULEULEULEULEUSERSERSERSERSERSERSERSERSERSERSERSERLEULEULEULEULEULEULEULEUASNASNASNASNASNASNASNASNGLUGLUGLUGLUGLUGLUGLUGLUGLULEULEULEULEULEULEULEULEUGLYGLYGLYGLYGLUGLUGLUGLUGLUGLUGLUGLUGLUARGARGARGARGARGARGARGARGARGARGARGGLNGLNGLNGLNGLNG

In [ ]:
print(mapped_residues)

{35: 673, 56: 675, 57: 675, 60: 676, 88: 680, 91: 680, 103: 681, 137: 687, 154: 690, 164: 691, 170: 692, 173: 692, 176: 692, 183: 693, 187: 694, 199: 695, 229: 700, 240: 701, 247: 702, 256: 703}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [673, 675, 675, 676, 680, 680, 681, 687, 690, 691, 692, 692, 692, 693, 694, 695, 700, 701, 702, 703]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/1t7r.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

#### 6IIU

In [ ]:
pdb_id = '6IIU'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

1349/1349 [==============================] - 604s 447ms/step
Predictions for 6IIU are complete.


In [ ]:
threshold = 0.001
well_predicted_dfs_by_pdb_id = {}

pdb_id = '6IIU'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 6IIU: 30


In [ ]:
df_6IIU = well_predicted_dfs_by_pdb_id['6IIU']
df_6IIU.head(2)

pdb_id           zinc_id  docking_score  \
1020    6IIU  ZINC001418324474     -12.741776   
14179   6IIU  ZINC001678963852     -12.726253   

                                                  smiles  \
1020      CO[C@H](C(=O)NC[C@@H](C)NCc1ocnc1C)c1ccc(F)cc1   
14179  CCc1ccc(-c2noc([C@H](C)NC(=O)NCc3ccc([Si](C)(C...   

                                                sequence  \
1020   DYKDDDDGAPADLEDNWETLNDNLKVIEKADNAAQVKDALTKMRAA...   
14179  DYKDDDDGAPADLEDNWETLNDNLKVIEKADNAAQVKDALTKMRAA...   

                                             encoded_seq  molecular_weight  \
1020   [3, 20, 9, 3, 3, 3, 3, 6, 1, 13, 1, 3, 10, 4, ...         -0.752505   
14179  [3, 20, 9, 3, 3, 3, 3, 6, 1, 13, 1, 3, 10, 4, ...          1.098231   

           logP  numH_donors  numH_acceptors  \
1020  -0.390013     0.687259        0.134442   
14179  1.342863     0.687259       -0.482460   

                               extended_connectivity_fps  \
1020   [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, ...   
14179  [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           node_features  \
1020   [6.0, 8.0, 6.0, 6.0, 8.0, 7.0, 6.0, 6.0, 6.0, ...   
14179  [6.0, 6.0, 6.0, 6.0, 6.0, 6.0, 6.0, 7.0, 8.0, ...   

                                           edge_features  \
1020   [1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
14179  [1.0, 1.0, 1.5, 1.5, 1.5, 1.0, 1.5, 1.5, 1.5, ...   

                                        adjacency_matrix  predicted_scores  \
1020   [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...        -12.740980   
14179  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...        -12.725389   

       difference  
1020     0.000796  
14179    0.000864

In [ ]:
X_text_input = np.array([np.array(x) for x in df_6IIU['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_6IIU['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_6IIU)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

157/157 [==============================] - 69s 441ms/step


In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           G     0.114373  [rec_229, rec_344, rec_229, rec_161, rec_260, ...   
1           L    -0.331355  [rec_414, rec_316, rec_414, rec_57, rec_185, r...   
2           K     0.180569        [rec_337, rec_336, rec_28, rec_337, rec_60]   
3           A     0.176876  [rec_397, rec_49, rec_132, rec_88, rec_49, rec...   
4           T    -0.493261  [rec_187, rec_40, rec_438, rec_18, rec_438, re...   
5           S    -0.049830  [rec_153, rec_307, rec_234, rec_224, rec_234, ...   
6           V     0.001451  [rec_405, rec_408, rec_459, rec_154, rec_372, ...   
7           R     0.033240  [rec_447, rec_465, rec_253, rec_254, rec_436, ...   
8           F     0.205368       [rec_290, rec_306, rec_302, rec_244, rec_70]   
9           N     0.632788      [rec_348, rec_424, rec_359, rec_122, rec_424]   
10          Y     0.792595                        [rec_347, rec_445, rec_445]   
11          Q     0.788087                                          [rec_453]   
12          P    -0.350440  [rec_55, rec_134, rec_273, rec_247, rec_55, re...   
13          E     0.262393  [rec_296, rec_17, rec_476, rec_27, rec_127, re...   
14          D    -0.370561  [rec_48, rec_355, rec_6, rec_353, rec_390, rec...   
15          C    -0.218238                                          [rec_174]   
16          I     0.367779                                          [rec_402]   

                                              Weights  
0   [1.2444137665953607, 0.7616679605723994, 0.314...  
1   [1.1875004590472544, 0.6330597717943789, 1.312...  
2   [1.1869602564698878, -1.0602398750183695, 0.40...  
3   [0.640473353676641, -1.509020194709017, 1.2095...  
4   [-0.9321382739473659, 0.7132165899625349, 0.49...  
5   [0.7176343705179898, 1.0867669237299398, -0.78...  
6   [-1.4728949632299213, -0.2637266757127254, 0.6...  
7   [1.3338433176396285, 0.8567819938974484, 0.964...  
8   [-1.0681362269902963, 0.8296350920556921, 1.15...  
9   [-0.9737530849386532, 0.6517807949718053, 0.83...  
10  [0.8098203579841925, 0.9961496764364082, 0.571...  
11                                [0.788086855056068]  
12  [0.4542425107144164, -0.6615591642883836, -0.6...  
13  [-1.372443929103084, -1.1282174116412962, 1.32...  
14  [-0.8370712427746795, -1.0839550368575908, -0....  
15                              [-0.2182379198801508]  
16                               [0.3677787313447689]

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           G     0.114373  [rec_229, rec_344, rec_229, rec_260, rec_239, ...   
2           K     0.180569                         [rec_337, rec_28, rec_337]   
3           A     0.176876  [rec_397, rec_132, rec_88, rec_49, rec_326, re...   
6           V     0.001451                        [rec_459, rec_154, rec_467]   
7           R     0.033240      [rec_447, rec_465, rec_253, rec_436, rec_465]   
8           F     0.205368                         [rec_306, rec_302, rec_70]   
9           N     0.632788               [rec_424, rec_359, rec_122, rec_424]   
10          Y     0.792595                        [rec_347, rec_445, rec_445]   
11          Q     0.788087                                          [rec_453]   
13          E     0.262393                [rec_476, rec_27, rec_127, rec_296]   
16          I     0.367779                                          [rec_402]   

                                              Weights  
0   [1.2444137665953607, 0.7616679605723994, 0.314...  
2   [1.1869602564698878, 0.40067556426291345, 0.87...  
3   [0.640473353676641, 1.209526647989822, 0.93177...  
6   [0.6643451015266195, 0.7638252001165495, 1.445...  
7   [1.3338433176396285, 0.8567819938974484, 0.964...  
8   [0.8296350920556921, 1.1567564957742518, 1.043...  
9   [0.6517807949718053, 0.8374975739138799, 1.079...  
10  [0.8098203579841925, 0.9961496764364082, 0.571...  
11                                [0.788086855056068]  
13  [1.324754330667046, 1.020839357431434, 0.87634...  
16                               [0.3677787313447689]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

['rec_229', 'rec_344', 'rec_229', 'rec_260', 'rec_239', 'rec_91', 'rec_161', 'rec_337', 'rec_28', 'rec_337', 'rec_397', 'rec_132', 'rec_88', 'rec_49', 'rec_326', 'rec_156', 'rec_49', 'rec_427', 'rec_397', 'rec_397', 'rec_137', 'rec_397', 'rec_146', 'rec_88', 'rec_459', 'rec_154', 'rec_467', 'rec_447', 'rec_465', 'rec_253', 'rec_436', 'rec_465', 'rec_306', 'rec_302', 'rec_70', 'rec_424', 'rec_359', 'rec_122', 'rec_424', 'rec_347', 'rec_445', 'rec_445', 'rec_453', 'rec_476', 'rec_27', 'rec_127', 'rec_296', 'rec_402']


In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [229, 344, 229, 260, 239, 91, 161, 337, 28, 337, 397, 132, 88, 49, 326, 156, 49, 427, 397, 397, 137, 397, 146, 88, 459, 154, 467, 447, 465, 253, 436, 465, 306, 302, 70, 424, 359, 122, 424, 347, 445, 445, 453, 476, 27, 127, 296, 402]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/6iiu.pdb'
input_sequence = 'DYKDDDDGAPADLEDNWETLNDNLKVIEKADNAAQVKDALTKMRAAALDAQKATPPKLEDKSPDSPEMKDFRHGFDILVGQIDDALKLANEGKVKEAQAAAEQLKTTRNAYIQKYLPCFRPTNITLEERRLIASPWFAASFCVVGLASNLLALSVLAGARQGGSHTRSSFLTFLCGLVLTDFLGLLVTGTIVVSQHAALFEWHAVDPGCRLCRFMGVVMIFFGLSPLLLGAAMASERYLGITRPFSRPAVASQRRAWATVGLVWAAALALGLLPLLGVGRYTVQYPGSWCFLTLGAESGDVAFGLLFSMLGGLSVGLSFLLNTVSVATLCHVYHGMKKYTCTVCGYIYNPEDGDPDNGVNPGTDFKDIPDDWVCPLCGVGKDQFEEVEERDSEVEMMAQALGIMVVASVCWLPLLVFIAQTVLRNPPAMSPAGQLSRTTEKELLIYLRVATWNQILDPWVYILFRRAVLRRLQPRLEFLEVLFQ'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

Alignments: [Alignment(seqA='ALAALAALAALAALAASPASPASPASPASPASPASPASPLEULEULEULEULEULEULEULEUGLUGLUGLUGLUGLUGLUGLUGLU-------GLUASPASPASPASPASPASPASPASPASNASNASNASNASNASNASNASNTRPTRPTRPTRPTRPTRPTRPTRPTRPTRPTRPTRPTRPTRPGLUGLUGLUGLUGLUGLUGLUGLUGLUTHRTHRTHRTHRTHRTHRTHRLEULEULEULEULEU-LEUL---EU-LEUASNASNASNASNASNASNASNASNASPASPASPASPASPASPASPASPASNASNASNASNASNASNASNAS-NLEULEULEULEULEULEULEULEULYSLYSLYSLYSLYSLYSLYSLYSLYSVALVALVALVALVALVAL-VALILEILEILEILEILEILEILEILEGLUGLUGLUGLUGLUGLUGLUGLUGLULYSLYSLYSLYSLYSLYSLYSLYSLYSALAALAALAALAALAASPASPASPASPASPASPASPASPASNASNASNASNASNASNASNASNALAALAALAALAALAALAALAALAALAAL-AGLNGLNGLNGLNGLNGLNGLNGLNGL-NVALVALVALVALVALVAL-VALLYSLYSLYSLYSLYSLYSLYSLYSLYSASPASPASPASPASPASPASPASPALAALAALAALAAL--ALEULEULEULEULEULEULEULEUTHRTHRTHRTHRTHRTHRTHRLYSLYSLYSLYSLYSLYSLYSLYSLYSMETMETMETMETMETMETMET-METARGARGARGARGARGARGARGARGARGARGARGALAALAALAALAALAALAALAALAALAALAALAALAALAALAALALEULEULEULEULEULEULEULEUASPASPASPASPASPASPASPASPALAALAALAALAALAGLNGLNGLNGLNGLNGLNGLNGLNGLNLYSLYS

In [ ]:
print(mapped_residues)

{27: 1004, 28: 1004, 49: 1007, 70: 1009, 88: 1011, 91: 1011, 122: 1015, 127: 1016, 132: 1016, 137: 1017, 146: 1018, 154: 1019, 156: 1019, 161: 1020, 229: 1030, 239: 1031, 253: 1033, 260: 1034, 296: 1039, 302: 1040, 306: 1040, 326: 1044, 337: 1045, 344: 1046, 347: 1047, 359: 1048, 397: 1053, 402: 1054, 424: 1057, 427: 1058, 436: 1059, 445: 1060, 447: 1061, 453: 1061, 459: 1062, 465: 1062, 467: 1062, 476: 1063}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [1004, 1004, 1007, 1009, 1011, 1011, 1015, 1016, 1016, 1017, 1018, 1019, 1019, 1020, 1030, 1031, 1033, 1034, 1039, 1040, 1040, 1044, 1045, 1046, 1047, 1048, 1053, 1054, 1057, 1058, 1059, 1060, 1061, 1061, 1062, 1062, 1062, 1063]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/6iiu.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

#### 6D6T

In [ ]:
pdb_id = '6D6T'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

425/425 [==============================] - 190s 447ms/step
Predictions for 6D6T are complete.


In [ ]:
threshold = 0.001
well_predicted_dfs_by_pdb_id = {}

pdb_id = '6D6T'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 6D6T: 0


In [ ]:
df_6D6T = well_predicted_dfs_by_pdb_id['6D6T']
df_6D6T.head(2)

In [ ]:
X_text_input = np.array([np.array(x) for x in df_6D6T['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_6D6T['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_6D6T)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

 38/157 [======>.......................] - ETA: 53s

In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           F     0.009436  [rec_199, rec_185, rec_330, rec_199, rec_290, ...   
1           N    -0.635343                                          [rec_302]   
2           Y     0.397473  [rec_337, rec_156, rec_96, rec_96, rec_337, re...   
3           E     0.277266  [rec_154, rec_146, rec_154, rec_154, rec_297, ...   
4           I     0.014723  [rec_187, rec_229, rec_115, rec_229, rec_229, ...   
5           D     0.394774  [rec_189, rec_170, rec_244, rec_170, rec_161, ...   
6           W     0.470268          [rec_91, rec_240, rec_91, rec_91, rec_91]   
7           L    -0.284642                [rec_82, rec_151, rec_296, rec_336]   
8           A    -0.491071  [rec_313, rec_44, rec_173, rec_173, rec_44, re...   
9           M     0.212613         [rec_48, rec_260, rec_48, rec_137, rec_48]   
10          S     0.321232  [rec_45, rec_228, rec_103, rec_103, rec_228, r...   
11          K    -0.239628                          [rec_12, rec_278, rec_20]   
12          R     0.281861                         [rec_85, rec_141, rec_141]   
13          T    -0.937213                        [rec_150, rec_178, rec_132]   
14          P     0.239525         [rec_205, rec_28, rec_28, rec_183, rec_28]   
15          V    -0.200733         [rec_35, rec_174, rec_35, rec_174, rec_52]   
16          C     0.598047                                 [rec_135, rec_149]   
17          G     0.271711                                 [rec_253, rec_176]   
18          Q     0.754607                                          [rec_308]   

                                              Weights  
0   [1.1098021275073722, 1.3447750034992942, -0.40...  
1                               [-0.6353429668642733]  
2   [0.5164448846294962, 1.1342860711868619, -0.71...  
3   [1.6257356638441713, -1.1996880559577654, 0.72...  
4   [-1.4725101382215302, 1.2952871289985113, -0.7...  
5   [-1.9327507739846475, -0.6257200988712329, 1.6...  
6   [1.639639640643247, 0.8967527314722572, 2.1637...  
7   [-1.4236141903941224, -0.5138944377720392, 0.3...  
8   [-1.1687042058992638, 0.04397060718115102, -1....  
9   [0.6881306674460373, 1.128818766841512, -0.155...  
10  [0.7777042096691583, -0.7651048200306948, 1.23...  
11  [-0.3325891069636022, -1.2354493939650737, 0.8...  
12  [-1.0761886982596187, 1.4021118758804771, 0.51...  
13  [-1.1874256061887551, -0.4336134361943662, -1....  
14  [1.0090902786734324, 0.2734519875611552, -1.00...  
15  [0.8515627197979446, -1.401053690954961, 1.203...  
16            [0.583206047195328, 0.6128889322564487]  
17           [-0.9757680727088763, 1.519189589309526]  
18                               [0.7546066428700593]

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           F     0.009436               [rec_199, rec_185, rec_199, rec_185]   
2           Y     0.397473               [rec_337, rec_156, rec_337, rec_298]   
3           E     0.277266               [rec_154, rec_154, rec_154, rec_154]   
4           I     0.014723      [rec_229, rec_229, rec_229, rec_229, rec_332]   
5           D     0.394774  [rec_244, rec_170, rec_161, rec_55, rec_88, re...   
6           W     0.470268                          [rec_91, rec_240, rec_91]   
9           M     0.212613                         [rec_48, rec_260, rec_137]   
10          S     0.321232       [rec_45, rec_103, rec_103, rec_307, rec_228]   
12          R     0.281861                                 [rec_141, rec_141]   
14          P     0.239525                          [rec_205, rec_28, rec_28]   
16          C     0.598047                                 [rec_135, rec_149]   
17          G     0.271711                                          [rec_176]   
18          Q     0.754607                                          [rec_308]   

                                              Weights  
0   [1.1098021275073722, 1.3447750034992942, 0.814...  
2   [0.5164448846294962, 1.1342860711868619, 1.360...  
3   [1.6257356638441713, 0.7236482309430703, 1.566...  
4   [1.2952871289985113, 0.9185619812818097, 0.273...  
5   [1.6711021378726307, 0.6984869513310246, 0.868...  
6   [1.639639640643247, 0.8967527314722572, 2.1637...  
9   [0.6881306674460373, 1.128818766841512, 1.4348...  
10  [0.7777042096691583, 1.2387262700180734, 1.466...  
12           [1.4021118758804771, 0.5196595203863146]  
14  [1.0090902786734324, 0.2734519875611552, 1.334...  
16            [0.583206047195328, 0.6128889322564487]  
17                                [1.519189589309526]  
18                               [0.7546066428700593]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [199, 185, 199, 185, 337, 156, 337, 298, 154, 154, 154, 154, 229, 229, 229, 229, 332, 244, 170, 161, 55, 88, 189, 55, 91, 240, 91, 48, 260, 137, 45, 103, 103, 307, 228, 141, 141, 205, 28, 28, 135, 149, 176, 308]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/6d6t.pdb'
input_sequence = 'QSVNDPSNMSLVKETVDRLLKGYDIRLRPDFGGPPVAVGMNIDIASIDMVSEVNMDYTLTMYFQQAWRDKRLSYNVIPLNLTLDNRVADQLWVPDTYFLNDKKSFVHGVTVKNRMIRLHPDGTVLYGLRITTTAACMMDLRRYPLDEQNCTLEIESYGYTTDDIEFYWRGDDNAVTGVTKIELPQFSIVDYKLITKKVVFSTGSYPRLSLSFKLKRNIGYFILQTYMPSILITILSWVSFWINYDASAARVALGITTVLTMTTINTHLRETLPKIPYVKAIDMYLMGCFVFVFMALLEYALVNYIFFSQPARAAAIDRWSRIFFPVVFSFFNIVYWLYYVN'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

In [ ]:
print(mapped_residues)

{12: 9, 22: 10, 28: 11, 56: 15, 78: 18, 82: 18, 88: 18, 100: 20, 111: 21, 153: 26, 156: 26, 189: 30, 201: 31, 224: 36, 229: 36, 234: 37, 256: 41, 274: 43, 303: 47, 316: 49, 332: 51}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [9, 10, 11, 15, 18, 18, 18, 20, 21, 26, 26, 30, 31, 36, 36, 37, 41, 43, 47, 49, 51]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/6d6t.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

Output hidden; open in https://colab.research.google.com to view.

#### 5EK0

In [ ]:
pdb_id = '5EK0'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]

    X_text_input = np.array([np.array(x) for x in df['encoded_seq'].tolist()])
    X_extended_connectivity_input = np.array(df['extended_connectivity_fps'].tolist())

    predictions = fingerprints_model.predict([X_text_input, X_extended_connectivity_input])
    df['predicted_scores'] = predictions
    test_dfs_by_pdb_id[pdb_id] = df
    print(f"Predictions for {pdb_id} are complete.")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

410/410 [==============================] - 182s 444ms/step
Predictions for 5EK0 are complete.


In [ ]:
threshold = 0.005
well_predicted_dfs_by_pdb_id = {}

pdb_id = '5EK0'

if pdb_id in test_dfs_by_pdb_id.keys():
    df = test_dfs_by_pdb_id[pdb_id]
    df['difference'] = abs(df['docking_score'] - df['predicted_scores'])

    well_predicted_df = df[df['difference'] <= threshold]
    well_predicted_dfs_by_pdb_id[pdb_id] = well_predicted_df
    print(f"Number of well-predicted data points for pdb_id {pdb_id}: {len(well_predicted_df)}")
else:
    print(f"PDB ID {pdb_id} not found in the dictionary.")

Number of well-predicted data points for pdb_id 5EK0: 23


In [ ]:
df_5EK0 = well_predicted_dfs_by_pdb_id['5EK0']
df_5EK0.head(2)

pdb_id           zinc_id  docking_score  \
7821    5EK0  ZINC001032285301      -9.087343   
10667   5EK0  ZINC001098734389      -9.016300   

                                          smiles  \
7821   C#CCCN1C[C@@H]2C[C@H]1CN2C(=O)c1cccc(C)n1   
10667   CCCCN1C[C@@H]2CCC[C@]2(NC(=O)c2cccn2C)C1   

                                                sequence  \
7821   MDYKDDDDKGSLVPRGSHMYLRITNIVESSFFTKFIIYLIVLNMVT...   
10667  MDYKDDDDKGSLVPRGSHMYLRITNIVESSFFTKFIIYLIVLNMVT...   

                                             encoded_seq  molecular_weight  \
7821   [11, 3, 20, 9, 3, 3, 3, 3, 9, 6, 16, 10, 18, 1...         -2.153531   
10667  [11, 3, 20, 9, 3, 3, 3, 3, 9, 6, 16, 10, 18, 1...         -1.727586   

           logP  numH_donors  numH_acceptors  \
7821  -0.986676    -1.428353       -1.099361   
10667 -0.159981    -0.370547       -1.099361   

                               extended_connectivity_fps  \
7821   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
10667  [0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           node_features  \
7821   [6.0, 6.0, 6.0, 6.0, 7.0, 6.0, 6.0, 6.0, 6.0, ...   
10667  [6.0, 6.0, 6.0, 6.0, 7.0, 6.0, 6.0, 6.0, 6.0, ...   

                                           edge_features  \
7821   [3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   
10667  [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, ...   

                                        adjacency_matrix  predicted_scores  \
7821   [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...         -9.082738   
10667  [[0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...         -9.019848   

       difference  
7821     0.004605  
10667    0.003548

In [ ]:
X_text_input = np.array([np.array(x) for x in df_5EK0['encoded_seq'].tolist()])
X_extended_connectivity_input = np.array(df_5EK0['extended_connectivity_fps'].tolist())

In [ ]:
explanations = []

for i in range(len(df_5EK0)):
    fingerprint_instance = X_extended_connectivity_input[i]
    text_instance = X_text_input[i]
    combined_instance = np.concatenate((fingerprint_instance, text_instance), axis=0)

    explanation = explainer.explain_instance(
        data_row=combined_instance,
        predict_fn=predict_fn
    )

    explanations.append((i, explanation))

157/157 [==============================] - 70s 443ms/step


In [ ]:
connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

for instance_index, explanation in explanations:
    print(f"Explanation for instance {instance_index + 1}:")

    weights = dict(explanation.as_list())

    fingerprint_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('bit_')}
    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    mapped_text_weights = {}
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = text_instance[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            if aa not in mapped_text_weights:
                mapped_text_weights[aa] = []
            mapped_text_weights[aa].append(weight)

    aggregated_weights = {aa: tuple(weights) for aa, weights in mapped_text_weights.items()}

    print("Original Sequence:", original_sequence)
    print("Mapped Receptor Weights:", aggregated_weights)
    print("Receptor Weights:", text_weights)
    print("Fingerprint Weights:", fingerprint_weights)
    print()

    explanation.show_in_notebook(show_table=True, show_all=False)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
all_aa_weights = defaultdict(list)

connectivity_feature_names = [f'bit_{i}' for i in range(X_extended_connectivity_input.shape[1])]
text_feature_names = [f'rec_{i}' for i in range(X_text_input.shape[1])]

# Process explanations and extract weights for each feature
for instance_index, explanation in explanations:
    weights = dict(explanation.as_list())

    text_weights = {feature: weight for feature, weight in weights.items() if feature.startswith('rec_')}

    # Decoding Sequences
    encoded_sequence = X_text_input[instance_index]
    original_sequence = decode_sequence(encoded_sequence)

    # Mapping receptors to their amino acid values at each position
    for feature, weight in text_weights.items():
        index_str = feature.split()[0].split('_')[1]
        index = int(index_str)
        aa_value = encoded_sequence[index]
        if aa_value != 0:
            aa = list(aa_alphabet.keys())[list(aa_alphabet.values()).index(aa_value)]
            rec_id = f'rec_{index}'
            all_aa_weights[aa].append((weight, rec_id))

# Mean weights for each amino acid
mean_aa_weights = {}
for aa, weights_recids in all_aa_weights.items():
    total_weight = sum(weight for weight, _ in weights_recids)
    mean_weight = total_weight / len(weights_recids)
    rec_ids = [rec_id for _, rec_id in weights_recids]
    weights_list = [weight for weight, _ in weights_recids]
    mean_aa_weights[aa] = (mean_weight, rec_ids, weights_list)

mean_aa_weights_df = pd.DataFrame(
    [(aa, mean_weight, rec_ids, weights_list) for aa, (mean_weight, rec_ids, weights_list) in mean_aa_weights.items()],
    columns=['Amino Acid', 'Mean Weight', 'rec_ids', 'Weights']
)

(mean_aa_weights_df)

Amino Acid  Mean Weight                                            rec_ids  \
0           I    -0.333044      [rec_174, rec_245, rec_244, rec_260, rec_152]   
1           F    -0.659923                 [rec_88, rec_229, rec_30, rec_199]   
2           P    -0.451241  [rec_228, rec_228, rec_228, rec_228, rec_228, ...   
3           L     0.017084  [rec_159, rec_240, rec_151, rec_167, rec_137, ...   
4           K     0.461433                        [rec_290, rec_290, rec_146]   
5           H     0.196381                                  [rec_267, rec_17]   
6           R     0.050119               [rec_279, rec_183, rec_183, rec_183]   
7           D    -0.609862  [rec_247, rec_269, rec_96, rec_269, rec_7, rec...   
8           S     0.235054  [rec_28, rec_153, rec_153, rec_194, rec_153, r...   
9           V    -0.078082  [rec_154, rec_48, rec_82, rec_125, rec_161, re...   
10          M    -0.722980                           [rec_47, rec_57, rec_57]   
11          E     0.314155                          [rec_49, rec_27, rec_217]   
12          Q     1.858899                                          [rec_178]   
13          G     0.425003                        [rec_132, rec_210, rec_189]   
14          T     0.792507                [rec_234, rec_234, rec_45, rec_234]   
15          Y    -0.500257                        [rec_196, rec_170, rec_196]   
16          W     1.238667                                          [rec_223]   
17          A    -1.187037                                          [rec_163]   
18          N     1.314658                                          [rec_273]   

                                              Weights  
0   [-1.6147723785069328, -0.6835832328131758, 1.3...  
1   [-1.44759858031722, -1.3139231942176537, 0.924...  
2   [-1.2799895224799456, -0.7793778861519647, -1....  
3   [-0.5502545202747671, 0.205747088298852, 1.093...  
4   [1.210280354630592, -1.1387347485859538, 1.312...  
5           [0.9542296091041143, -0.5614671151483749]  
6   [-0.8089571931170492, -1.5114770125005978, 1.1...  
7   [1.2434645596131981, -1.458755233129933, -0.74...  
8   [-1.2893412591305953, 0.9626630756943116, 1.03...  
9   [1.1570071931514367, -1.691015605797027, -1.45...  
10  [-0.525802104571614, -1.3460783012183253, -0.2...  
11  [1.3266732910717682, -1.1367544033541772, 0.75...  
12                               [1.8588991438409863]  
13  [1.39949157435113, -0.9336150830346684, 0.8091...  
14  [-0.013797309765476622, 1.159412564138409, 1.2...  
15  [-1.1842404445765822, -0.8878674712583011, 0.5...  
16                               [1.2386673929551557]  
17                              [-1.1870366490508306]  
18                               [1.3146581902311874]

In [ ]:
def filter_positive_weights(row):
    positive_indices = [i for i, weight in enumerate(row['Weights']) if weight > 0]
    filtered_weights = [row['Weights'][i] for i in positive_indices]
    filtered_rec_ids = [row['rec_ids'][i] for i in positive_indices]
    return pd.Series({'Amino Acid': row['Amino Acid'], 'Mean Weight': row['Mean Weight'],
                      'rec_ids': filtered_rec_ids, 'Weights': filtered_weights})

positive_mean_weight_df = mean_aa_weights_df[mean_aa_weights_df['Mean Weight'] > 0]
filtered_df = positive_mean_weight_df.apply(filter_positive_weights, axis=1)
filtered_df = filtered_df[filtered_df['Weights'].map(len) > 0]
(filtered_df)

Amino Acid  Mean Weight                                        rec_ids  \
3           L     0.017084           [rec_240, rec_151, rec_167, rec_137]   
4           K     0.461433                             [rec_290, rec_146]   
5           H     0.196381                                      [rec_267]   
6           R     0.050119                             [rec_183, rec_183]   
8           S     0.235054  [rec_153, rec_153, rec_194, rec_153, rec_153]   
11          E     0.314155                              [rec_49, rec_217]   
12          Q     1.858899                                      [rec_178]   
13          G     0.425003                             [rec_132, rec_189]   
14          T     0.792507                     [rec_234, rec_45, rec_234]   
16          W     1.238667                                      [rec_223]   
18          N     1.314658                                      [rec_273]   

                                              Weights  
3   [0.205747088298852, 1.0938386539472078, 1.1493...  
4             [1.210280354630592, 1.3127520256690965]  
5                                [0.9542296091041143]  
6            [1.1983045654097106, 1.3226062165710948]  
8   [0.9626630756943116, 1.0383099638685815, 1.017...  
11           [1.3266732910717682, 0.7525459520636991]  
12                               [1.8588991438409863]  
13             [1.39949157435113, 0.8091323750416894]  
14  [1.159412564138409, 1.2951889229031408, 0.7292...  
16                               [1.2386673929551557]  
18                               [1.3146581902311874]

In [ ]:
all_rec_ids = []
for rec_ids in filtered_df['rec_ids']:
    all_rec_ids.extend(rec_ids)

print(all_rec_ids)

['rec_240', 'rec_151', 'rec_167', 'rec_137', 'rec_290', 'rec_146', 'rec_267', 'rec_183', 'rec_183', 'rec_153', 'rec_153', 'rec_194', 'rec_153', 'rec_153', 'rec_49', 'rec_217', 'rec_178', 'rec_132', 'rec_189', 'rec_234', 'rec_45', 'rec_234', 'rec_223', 'rec_273']


In [ ]:
positive_residues = []

for rec_id in all_rec_ids:
    residue_index = int(rec_id.split('_')[1])
    positive_residues.append(residue_index)

print("Residue indices:", positive_residues)

Residue indices: [240, 151, 167, 137, 290, 146, 267, 183, 183, 153, 153, 194, 153, 153, 49, 217, 178, 132, 189, 234, 45, 234, 223, 273]


In [ ]:
def map_positions_to_residues(pdb_file, input_sequence, positions):
    # Parse PDB file to extract sequence and residue numbers
    with open(pdb_file, 'r') as f:
        pdb_seq = ''
        residue_numbers = []
        for line in f:
            if line.startswith('ATOM'):
                residue_numbers.append(int(line[22:26].strip()))
                pdb_seq += line[17:20].strip()

    # Perform pairwise alignment
    alignments = align.globalxx(pdb_seq, input_sequence)
    print("Alignments:", alignments)

    # Extract residue numbers corresponding to aligned positions
    mapped_residues = {}
    pdb_pos = 0
    for i, char in enumerate(alignments[0][0]):
        if char != '-':
            pdb_pos += 1
        if pdb_pos in positions:
            mapped_residues[pdb_pos] = residue_numbers[pdb_pos - 1]

    return mapped_residues

pdb_file = '/content/drive/MyDrive/PDB_files/5ek0.pdb'
input_sequence = 'MDYKDDDDKGSLVPRGSHMYLRITNIVESSFFTKFIIYLIVLNMVTMMVEKEGQSQHMTEVLYWINVVFIILFTIEIILRIYVHRISFFKDPWSLFDFVVVIISIVGMFLADLIETYFVSPTLFRVIRLARIGRILRLVTAVPQMRKIVSALISVIPGMLSVIALMTLFFYIFAIMATQLFGERFPEWFGTLGESFYTLFQVMTLESWSMGIVRPLMEVYPYAWVFFIPFIFVVTFVMINLVVAIIVDAMAILNQKEEQHIIDEVQSHEDNINNEIIKLREEIVELKELIKTSLKN'
positions = positive_residues

mapped_residues = map_positions_to_residues(pdb_file, input_sequence, positions)

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
print(mapped_residues)

{45: 1493, 49: 1494, 132: 1504, 137: 1505, 146: 1505, 151: 1506, 153: 1506, 167: 1508, 178: 1509, 183: 1509, 189: 1510, 194: 1511, 217: 1513, 223: 1514, 234: 1515, 240: 1516, 267: 1519, 273: 1520, 290: 1522}


In [ ]:
residue_list = list(mapped_residues.values())
print("Residue indices:", residue_list)

Residue indices: [1493, 1494, 1504, 1505, 1505, 1506, 1506, 1508, 1509, 1509, 1510, 1511, 1513, 1514, 1515, 1516, 1519, 1520, 1522]


In [ ]:
protein_structure = open('/content/drive/MyDrive/PDB_files/5ek0.pdb', 'r').read()

view = py3Dmol.view(width=800, height=600)
view.addModel(protein_structure, 'pdb')

view.setStyle({'cartoon': {'color': 'spectrum'}})

highlight_residues = residue_list

for res in highlight_residues:
    view.addSurface(py3Dmol.SAS, {'opacity': 0.7, 'color': 'black'}, {'resi': res})

view.zoomTo()
view.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.